# PPAC 信号处理

### 实验设置
 ![setup](setup.png) 
 
### delayline PPAC 信号定义:
![PPAC](ppac_delayline.png)

$t_{xl}=(l/2+x)T_{delay}/l$

$t_{xr}=(l/2-x)T_{delay}/l$

$x=\frac{(t_{xl}-t_{xr})l}{2T_{delay}}$

$t_{xl}+t_{xr}=T_{delay}$

$T_{delay}$ is total delay time of the delaylines with length of $l$
### 两种类型PPAC
实验中采用了两种不同规格尺寸的 PPAC，一种是double PPAC(F8PPAC1, F8PPAC2), 面积为 $240 × 150 mm^2$ 
另一种是single PPAC(F8PPAC3), 面积为 $100 × 100 mm^2$。

### 文件中TreeBranch的定义: 
$F8PPACRawData[i][j]$ -Raw Data

$i: 0-PPAC1A, 1-PPAC1B, 2-PPAC2A, 3-PPAC2B, 4-PPAC3$

$j: 0-t_{xl}, 1-t_{xr}, 2-t_{yd}, 3-t_{yu}, 4-t_{a}, 5-q_{xl}, 6-q_{xr}, 7-q_{yd}, 8-q_{yu}, 9-q_{a}$


$PPACF8[i][k]$ -Calibrated Data


| Branch | PPAC |
| --------------- | ------------------------------- | 
| PPACF8[0][0] | PPAC 1 Layer A X (mm) |
| PPACF8[0][1] | PPAC 1 Layer A Y (mm) |
|PPACF8[0][2] | PPAC 1 Layer A Z for X direction (mm) |
|PPACF8[0][3] | PPAC 1 Layer A Z for Y direction (mm) |
|PPACF8[0][4]| PPAC 1 Layer A Anode time (ns) |
|PPACF8[1][0]| PPAC 1 Layer B X (mm) |
|PPACF8[1][1]| PPAC 1 Layer B Y (mm) |
|PPACF8[1][2]| PPAC 1 Layer B Z for X direction (mm) |
|PPACF8[1][3]| PPAC 1 Layer B Z for Y direction (mm) |
|PPACF8[1][4]| PPAC 1 Layer B Anode time (ns) |
|PPACF8[2][*]| PPAC 2 Layer A *|
|PPACF8[3][*]| PPAC 2 Layer B *|
|PPACF8[4][*]| PPAC 3 *|

## PPAC 信号分析
Trigger(time start): Plastic scintillator 

$T_{xl}=L/v+t_{xl}+t_{xloff}$// v dependence

$T_{xr}=L/v+t_{xr}+t_{xroff}$ 

$T_{xl}+T_{xr}=2L/v+T_{delay}+(t_{xloff}+t_{xroff})$ // v dependence

$T_{a}=L/v+t_{aoff}$

$Tt_{xl}=T_{xl}-T_a=t_{xl}+(t_{xloff}+t_{aoff})$ 

$Tt_{xr}=T_{xr}-T_a=t_{xr}+(t_{xroff}+t_{aoff})$ 

$Tt_{xl}-Tt_{xr}=t_{xl}-t_{xr}+(t_{xloff}-t_{xroff})$ 

$Tt_{xl}+Tt_{xr}=t_{xl}+t_{xr}+(t_{xloff}+t_{xroff}-2t_{aoff})$=Const.

## PPAC postion calibration
   - Determine  ns2mm  by Mask with alpha source
   - Determine  position shift by Beam with slit 
![TDC](ppacpos.png)

In [1]:
%jsroot on
TFile *ipf=new TFile("run0005.root");//  $HOME/data/MUST2@BigRIPS/ROOTFILE/
TTree *tree=(TTree*) ipf->Get("tree");

In [2]:
TCanvas *c1=new TCanvas("c1","c1");
tree->Draw("F8PPACRawData[0][0]>>hxl(1000,0,5000)");//F8PPAC1A-txl
hxl->Draw();
c1->SetLogy();
c1->Draw();//图中4095道的位置对应TDC的超界信号

In [3]:
tree->Draw("F8PPACRawData[0][4]>>ha(5000,0,5000)");//F8PPAC1A-ta
ha->Draw();
c1->Draw();//PPAC的阳极时间信号

In [4]:
// F8PPAC
  tree->SetAlias("Txl","F8PPACRawData[0][0]");//F8PPAC1A-txl
  tree->SetAlias("Txr","F8PPACRawData[0][1]");//F8PPAC1A-txr
  tree->SetAlias("Tyd","F8PPACRawData[0][2]");//F8PPAC1A-tyu
  tree->SetAlias("Tyu","F8PPACRawData[0][3]");//F8PPAC1A-tyd
  tree->SetAlias("Ta","F8PPACRawData[0][4]");//F8PPAC1A-Anode

  tree->SetAlias("Ttxl","Txl-Ta");
  tree->SetAlias("Ttxr","Txr-Ta");
  tree->SetAlias("Ttyd","Tyd-Ta");
  tree->SetAlias("Ttyu","Tyu-Ta");
  tree->SetAlias("sum","Txl+Txr");
  TCut cxl="Txl>0 && Txl<4000";
  TCut cxr="Txr>0 && Txr<4000";
  TCut cyu="Tyu>0 && Tyu<4000";
  TCut cyd="Tyd>0 && Tyd<4000";
  TCut ca="Ta>0 && Ta<4000";
  TCut cf8ppac=cxl && cxr && cyu && cyd && ca;

In [5]:
tree->Draw("Txl-Txr");//with no proper range cut
c1->Draw();

In [6]:
tree->Draw("Txl-Txr",cxl&&cxr);//with proper range cut
c1->Draw();

In [7]:
tree->Draw("Txl:Txr>>(1000,0,2500,1000,0,2500)",cxl && cxr,"colz");
gStyle->SetPalette(1);
c1->SetLogy(0);
c1->Draw();

In [8]:
tree->Draw("Ttxl:Ttxr>>(1000,0,2500,1000,0,2500)",cxl && cxr && ca,"colz");
gStyle->SetPalette(1);
c1->Draw();

### Pile-up Cut
在束流比较强的时候，需要考虑堆积(Pile-up)事件的排除。堆积是由于同时有多个粒子打在PPAC上，造成delayline的x或y的两端的时间不对应同一个粒子。
这种时间的特征是delayline的两端信号传输时间和不在是常数。假设a粒子到达时间是Ta，b粒子到达时间是Tb，则当|Tb-Ta|<Tdelay时可产生堆积信号。
 ![multihit](pileup.png) 

In [9]:
TCut cpile="abs(Ttxl+Ttxr-1172)<24";
tree->Draw("Ttxr-Ttxl:Ttyu-Ttyd>>(1000,-1000,1000,1000,-1000,1000)",cxl&&cxr&&ca&&cpile,"colz");//ppac xy with raw data
c1->Draw();

In [10]:
tree->Draw("PPACF8[0][0]:PPACF8[0][1]>>(1000,-100,100,1000,-100,100)","PPACF8[0][4]>0","colz");//calibrated PPAC x-y
c1->Draw();